In [3]:
import control as ct
import numpy as np
import scipy as sc

In [5]:
import pymor

In [9]:
import pymor.discretizations.iosys as iosys

In [11]:
help(iosys.LTISystem.from_matrices)

Help on method from_matrices in module pymor.discretizations.iosys:

from_matrices(A, B, C, D=None, E=None, cont_time=True, input_id='INPUT', state_id='STATE', output_id='OUTPUT', solver_options=None, estimator=None, visualizer=None, cache_region='memory', name=None) method of pymor.core.interfaces.ImmutableMeta instance
    Create |LTISystem| from matrices.
    
    Parameters
    ----------
    A
        The |NumPy array| or |SciPy spmatrix| A.
    B
        The |NumPy array| or |SciPy spmatrix| B.
    C
        The |NumPy array| or |SciPy spmatrix| C.
    D
        The |NumPy array| or |SciPy spmatrix| D or `None` (then D is
        assumed to be zero).
    E
        The |NumPy array| or |SciPy spmatrix| E or `None` (then E is
        assumed to be identity).
    cont_time
        `True` if the system is continuous-time, otherwise `False`.
    input_id
        Id of the input space.
    state_id
        Id of the state space.
    output_id
        Id of the output space.
    solver_

In [12]:
from pymor.basic import *
from pymor.core.config import config
set_log_levels({'pymor.algorithms.gram_schmidt.gram_schmidt': 'WARNING'})


In [13]:
p = InstationaryProblem(
    StationaryProblem(
        domain=LineDomain([0.,1.], left='robin', right='robin'),
        diffusion=ConstantFunction(1., 1),
        robin_data=(ConstantFunction(1., 1), ExpressionFunction('(x[...,0] < 1e-10) * 1.', 1)),
        functionals={'output': ('l2_boundary', ExpressionFunction('(x[...,0] > (1 - 1e-10)) * 1.', 1))}
    ),
    ConstantFunction(0., 1),
    T=3.
)

d, _ = discretize_instationary_cg(p, diameter=1/100, nt=100)

09:25 L2ProductP1: Integrate the products of the shape functions on each element
09:25 L2ProductP1: Determine global dofs ...
09:25 L2ProductP1: Boundary treatment ...
09:25 L2ProductP1: Assemble system matrix ...
09:25 L2ProductP1: Integrate the products of the shape functions on each element
09:25 L2ProductP1: Determine global dofs ...
09:25 L2ProductP1: Boundary treatment ...
09:25 L2ProductP1: Assemble system matrix ...
09:25 DiffusionOperatorP1: Calulate gradients of shape functions transformed by reference map ...
09:25 DiffusionOperatorP1: Calculate all local scalar products beween gradients ...
09:25 DiffusionOperatorP1: Determine global dofs ...
09:25 DiffusionOperatorP1: Boundary treatment ...
09:25 DiffusionOperatorP1: Assemble system matrix ...
09:25 DiffusionOperatorP1: Calulate gradients of shape functions transformed by reference map ...
09:25 DiffusionOperatorP1: Calculate all local scalar products beween gradients ...
09:25 DiffusionOperatorP1: Determine global dofs ..

In [14]:
lti = d.to_lti()

In [15]:
from pymor.algorithms.to_matrix import to_matrix

In [18]:
A = to_matrix(lti.A,format='dense')
B = to_matrix(lti.B,format='dense')
C = to_matrix(lti.C,format='dense')
D = to_matrix(lti.D,format='dense')

In [17]:
lti

array([[-101.,  100.,    0., ...,    0.,    0.,    0.],
       [ 100., -200.,  100., ...,    0.,    0.,    0.],
       [   0.,  100., -200., ...,    0.,    0.,    0.],
       ...,
       [   0.,    0.,    0., ..., -200.,  100.,    0.],
       [   0.,    0.,    0., ...,  100., -200.,  100.],
       [   0.,    0.,    0., ...,    0.,  100., -101.]])

In [19]:
lti.hinf_norm()

0.33333333333389215